In [ ]:
# Check if TF is using gpu
from tensorflow.python.client import device_lib
print(device_lib.list_local_devices())

# Project: Train a Quadcopter How to Fly

Design an agent to fly a quadcopter, and then train it using a reinforcement learning algorithm of your choice! 

Try to apply the techniques you have learnt, but also feel free to come up with innovative ideas and test them.

## Instructions

Take a look at the files in the directory to better understand the structure of the project. 

- `task.py`: Define your task (environment) in this file.
- `agents/`: Folder containing reinforcement learning agents.
    - `policy_search.py`: A sample agent has been provided here.
    - `agent.py`: Develop your agent here.
- `physics_sim.py`: This file contains the simulator for the quadcopter.  **DO NOT MODIFY THIS FILE**.

For this project, you will define your own task in `task.py`.  Although we have provided a example task to get you started, you are encouraged to change it.  Later in this notebook, you will learn more about how to amend this file.

You will also design a reinforcement learning agent in `agent.py` to complete your chosen task.  

You are welcome to create any additional files to help you to organize your code.  For instance, you may find it useful to define a `model.py` file defining any needed neural network architectures.

## Controlling the Quadcopter

We provide a sample agent in the code cell below to show you how to use the sim to control the quadcopter.  This agent is even simpler than the sample agent that you'll examine (in `agents/policy_search.py`) later in this notebook!

The agent controls the quadcopter by setting the revolutions per second on each of its four rotors.  The provided agent in the `Basic_Agent` class below always selects a random action for each of the four rotors.  These four speeds are returned by the `act` method as a list of four floating-point numbers.  

For this project, the agent that you will implement in `agents/agent.py` will have a far more intelligent method for selecting actions!

In [ ]:
import random

class Basic_Agent():
    def __init__(self, task):
        self.task = task
    
    def act(self):
        new_thrust = random.gauss(450., 25.)
        return [new_thrust + random.gauss(0., 1.) for x in range(4)]

Run the code cell below to have the agent select actions to control the quadcopter.  

Feel free to change the provided values of `runtime`, `init_pose`, `init_velocities`, and `init_angle_velocities` below to change the starting conditions of the quadcopter.

The `labels` list below annotates statistics that are saved while running the simulation.  All of this information is saved in a text file `data.txt` and stored in the dictionary `results`.  

In [ ]:
%load_ext autoreload
%autoreload 2

import csv
import numpy as np
from task import Task

# Modify the values below to give the quadcopter a different starting position.
runtime = 5.                                     # time limit of the episode
init_pose = np.array([0., 0., 10., 0., 0., 0.])  # initial pose
init_velocities = np.array([0., 0., 0.])         # initial velocities
init_angle_velocities = np.array([0., 0., 0.])   # initial angle velocities
file_output = 'data.txt'                         # file name for saved results

# Setup
task = Task(init_pose, init_velocities, init_angle_velocities, runtime)
agent = Basic_Agent(task)
done = False
labels = ['time', 'x', 'y', 'z', 'phi', 'theta', 'psi', 'x_velocity',
          'y_velocity', 'z_velocity', 'phi_velocity', 'theta_velocity',
          'psi_velocity', 'rotor_speed1', 'rotor_speed2', 'rotor_speed3', 'rotor_speed4']
results = {x : [] for x in labels}

# Run the simulation, and save the results.
with open(file_output, 'w') as csvfile:
    writer = csv.writer(csvfile)
    writer.writerow(labels)
    while True:
        rotor_speeds = agent.act()
        _, _, done = task.step(rotor_speeds)
        to_write = [task.sim.time] + list(task.sim.pose) + list(task.sim.v) + list(task.sim.angular_v) + list(rotor_speeds)
        for ii in range(len(labels)):
            results[labels[ii]].append(to_write[ii])
        writer.writerow(to_write)
        if done:
            break

Run the code cell below to visualize how the position of the quadcopter evolved during the simulation.

In [ ]:
import matplotlib.pyplot as plt
%matplotlib inline

plt.plot(results['time'], results['x'], label='x')
plt.plot(results['time'], results['y'], label='y')
plt.plot(results['time'], results['z'], label='z')
plt.legend()
_ = plt.ylim()

The next code cell visualizes the velocity of the quadcopter.

In [ ]:
plt.plot(results['time'], results['x_velocity'], label='x_hat')
plt.plot(results['time'], results['y_velocity'], label='y_hat')
plt.plot(results['time'], results['z_velocity'], label='z_hat')
plt.legend()
_ = plt.ylim()

Next, you can plot the Euler angles (the rotation of the quadcopter over the $x$-, $y$-, and $z$-axes),

In [ ]:
plt.plot(results['time'], results['phi'], label='phi')
plt.plot(results['time'], results['theta'], label='theta')
plt.plot(results['time'], results['psi'], label='psi')
plt.legend()
_ = plt.ylim()

before plotting the velocities (in radians per second) corresponding to each of the Euler angles.

In [ ]:
plt.plot(results['time'], results['phi_velocity'], label='phi_velocity')
plt.plot(results['time'], results['theta_velocity'], label='theta_velocity')
plt.plot(results['time'], results['psi_velocity'], label='psi_velocity')
plt.legend()
_ = plt.ylim()

Finally, you can use the code cell below to print the agent's choice of actions.  

In [ ]:
plt.plot(results['time'], results['rotor_speed1'], label='Rotor 1 revolutions / second')
plt.plot(results['time'], results['rotor_speed2'], label='Rotor 2 revolutions / second')
plt.plot(results['time'], results['rotor_speed3'], label='Rotor 3 revolutions / second')
plt.plot(results['time'], results['rotor_speed4'], label='Rotor 4 revolutions / second')
plt.legend()
_ = plt.ylim()

When specifying a task, you will derive the environment state from the simulator.  Run the code cell below to print the values of the following variables at the end of the simulation:
- `task.sim.pose` (the position of the quadcopter in ($x,y,z$) dimensions and the Euler angles),
- `task.sim.v` (the velocity of the quadcopter in ($x,y,z$) dimensions), and
- `task.sim.angular_v` (radians/second for each of the three Euler angles).

In [ ]:
# the pose, velocity, and angular velocity of the quadcopter at the end of the episode
print(task.sim.pose)
print(task.sim.v)
print(task.sim.angular_v)

In the sample task in `task.py`, we use the 6-dimensional pose of the quadcopter to construct the state of the environment at each timestep.  However, when amending the task for your purposes, you are welcome to expand the size of the state vector by including the velocity information.  You can use any combination of the pose, velocity, and angular velocity - feel free to tinker here, and construct the state to suit your task.

## The Task

A sample task has been provided for you in `task.py`.  Open this file in a new window now. 

The `__init__()` method is used to initialize several variables that are needed to specify the task.  
- The simulator is initialized as an instance of the `PhysicsSim` class (from `physics_sim.py`).  
- Inspired by the methodology in the original DDPG paper, we make use of action repeats.  For each timestep of the agent, we step the simulation `action_repeats` timesteps.  If you are not familiar with action repeats, please read the **Results** section in [the DDPG paper](https://arxiv.org/abs/1509.02971).
- We set the number of elements in the state vector.  For the sample task, we only work with the 6-dimensional pose information.  To set the size of the state (`state_size`), we must take action repeats into account.  
- The environment will always have a 4-dimensional action space, with one entry for each rotor (`action_size=4`). You can set the minimum (`action_low`) and maximum (`action_high`) values of each entry here.
- The sample task in this provided file is for the agent to reach a target position.  We specify that target position as a variable.

The `reset()` method resets the simulator.  The agent should call this method every time the episode ends.  You can see an example of this in the code cell below.

The `step()` method is perhaps the most important.  It accepts the agent's choice of action `rotor_speeds`, which is used to prepare the next state to pass on to the agent.  Then, the reward is computed from `get_reward()`.  The episode is considered done if the time limit has been exceeded, or the quadcopter has travelled outside of the bounds of the simulation.

In the next section, you will learn how to test the performance of an agent on this task.

## The Agent

The sample agent given in `agents/policy_search.py` uses a very simplistic linear policy to directly compute the action vector as a dot product of the state vector and a matrix of weights. Then, it randomly perturbs the parameters by adding some Gaussian noise, to produce a different policy. Based on the average reward obtained in each episode (`score`), it keeps track of the best set of parameters found so far, how the score is changing, and accordingly tweaks a scaling factor to widen or tighten the noise.

Run the code cell below to see how the agent performs on the sample task.

In [2]:
import sys
import pandas as pd
from agents.policy_search import PolicySearch_Agent
from task import Task

num_episodes = 1

target_pos = np.array([50., 50., 50.])
init_pos = np.array([0., 0., 0., 0., 0., 0.])
task = Task(target_pos=target_pos)
agent = PolicySearch_Agent(task) 

for i_episode in range(1, num_episodes+1):
    state = agent.reset_episode() # start a new episode
    while True:
        action = agent.act(state) 
        next_state, reward, done = task.step(action)
        agent.step(reward, done)
        state = next_state
        if done:
            print("\rEpisode = {:4d}, score = {:7.3f} (best = {:7.3f}), noise_scale = {}".format(
                i_episode, agent.score, agent.best_score, agent.noise_scale), end="")  # [debug]
            break
    sys.stdout.flush()

None None None 5.0 [ 50.  50.  50.]
x: 0.0, y: 0.0 z: 10.0
x: 0.0, y: 0.0 z: 10.00800682237759
x: -0.008286375721631559, y: 0.003968136602345874 z: 10.025923843629464
x: -0.019350469061104287, y: 0.003673635702938738 z: 10.042723255876684
x: -0.0214401578428348, y: 0.005666997968699326 z: 10.052641741025777
x: -0.0266287816028167, y: 0.010325979202485507 z: 10.052103480072821
x: -0.04961734401657269, y: 0.007070066045959758 z: 10.04307875857957
x: -0.09217112009245472, y: 0.0012081059154325372 z: 10.035623791575247
x: -0.15321425751276946, y: -0.007853879454187388 z: 10.03042120707776
x: -0.23147471030211314, y: -0.010922922267870148 z: 10.025313001037615
x: -0.31754604568729067, y: 0.003636300331873848 z: 10.012445043829636
x: -0.3993259014501444, y: 0.037519540761845195 z: 9.997262920523179
x: -0.4885527862578076, y: 0.08305018775461291 z: 9.986762305204618
x: -0.5959080865738284, y: 0.12421396877715249 z: 9.974325963876204
x: -0.7024645955681889, y: 0.15071249111980517 z: 9.96007142

This agent should perform very poorly on this task.  And that's where you come in!

## Define the Task, Design the Agent, and Train Your Agent!

Amend `task.py` to specify a task of your choosing.  If you're unsure what kind of task to specify, you may like to teach your quadcopter to takeoff, hover in place, land softly, or reach a target pose.  

After specifying your task, use the sample agent in `agents/policy_search.py` as a template to define your own agent in `agents/agent.py`.  You can borrow whatever you need from the sample agent, including ideas on how you might modularize your code (using helper methods like `act()`, `learn()`, `reset_episode()`, etc.).

Note that it is **highly unlikely** that the first agent and task that you specify will learn well.  You will likely have to tweak various hyperparameters and the reward function for your task until you arrive at reasonably good behavior.

As you develop your agent, it's important to keep an eye on how it's performing. Use the code above as inspiration to build in a mechanism to log/save the total rewards obtained in each episode to file.  If the episode rewards are gradually increasing, this is an indication that your agent is learning.

In [8]:
## TODO: Train your agent here.
from agents.DDPG import DDPG
import numpy as np
import sys
import pandas as pd

num_episodes = 100
initial_pos = np.array([0., 0., 20., 0., 0., 0.])
initial_velocity = (0., 0., 20.)

run_time= 5.0
target_pos = np.array([0., 0., 30.])
task = Task(target_pos=target_pos)
agent = DDPG(task) 


# Results log
results = {x : [] for x in labels}
# Best reward initialized is negative infinity
highest_score = -np.Inf

file_output = 'results-ddpg.txt'
# Setting up the writer
with open(file_output, 'w') as csvfile:
    writer = csv.writer(csvfile)
    writer.writerow(labels)
    
    for i_episode in range(1, num_episodes+1):
        state = agent.reset_episode() # start a new episode

        total_reward = 0
        while True:
            action = agent.act(state) 
            next_state, reward, done = task.step(action)
            
            # Calculating the total reward
            total_reward += reward
            to_write = [task.sim.time] + list(task.sim.pose) + list(task.sim.v) + list(task.sim.angular_v) + list(rotor_speeds)
            
            agent.step(action, reward, next_state, done)
            state = next_state
            
            for ii in range(len(labels)):
                results[labels[ii]].append(to_write[ii])
                writer.writerow(to_write)
            
            if done:
                if (total_reward > highest_score):
                    highest_score = total_reward
                print("Episode: {}  Reward: {} highScore: {}".format(i_episode, total_reward, highest_score))
                print(to_write)
                break
        sys.stdout.flush()

None None None 5.0 [  0.   0.  30.]
x: 0.0, y: 0.0 z: 10.0
x: 0.0, y: 0.0 z: 9.999619723676002
x: -0.0015519586777368024, y: -5.429673201042697e-07 z: 9.996591851764485
x: -0.004044672746333679, y: -5.075369142034262e-06 z: 9.987876213260757
x: -0.004551540373666034, y: -1.1573347817895642e-05 z: 9.974623064488293
x: -0.004650285304514898, y: -1.8804477499096806e-05 z: 9.959580409056137
x: -0.0070481955540371115, y: -2.3272884032339015e-05 z: 9.94099508730273
x: -0.010278902709068652, y: -1.126548535194269e-05 z: 9.916371582597167
x: -0.011734844455642083, y: 1.5575246149420446e-05 z: 9.886302488780846
x: -0.010819860989139765, y: 3.631878800295575e-05 z: 9.852704490444559
x: -0.008455100379605882, y: 2.6044220671184877e-05 z: 9.817116548468828
x: -0.006241012337606667, y: -3.690545149206312e-05 z: 9.779994274827448
x: -0.005632842716250439, y: -0.00015520208471550347 z: 9.740783274662189
x: -0.007383555580222964, y: -0.0002974483598454056 z: 9.698309563615526
x: -0.011532023514894218,

x: 0.0, y: 0.0 z: 10.0
x: 0.0, y: 0.0 z: 9.999621517267613
x: -0.0015527486273225542, y: -5.39799658038373e-07 z: 9.99659199737607
x: -0.0040372309206182354, y: -4.963434633819737e-06 z: 9.98787167139669
x: -0.004531953049409305, y: -1.1294619744766303e-05 z: 9.974629759712018
x: -0.004645214669253911, y: -1.8435517442464983e-05 z: 9.95959920178173
x: -0.00706154634758657, y: -2.2692267276699405e-05 z: 9.940985182801084
x: -0.010262974192326711, y: -1.0466637920242866e-05 z: 9.916314705362716
x: -0.011646806237074942, y: 1.6024282862204198e-05 z: 9.886245758537312
x: -0.010670375096096807, y: 3.559737396041514e-05 z: 9.85272325152731
x: -0.008311978518982443, y: 2.3737772791370196e-05 z: 9.817262654312806
x: -0.006195175107963469, y: -4.005904198846285e-05 z: 9.780264480496529
x: -0.005758499838161633, y: -0.0001567404490933718 z: 9.741118716796523
x: -0.007710250255136526, y: -0.0002934108333958837 z: 9.698619633118078
x: -0.012040833325865306, y: -0.00039799839691178045 z: 9.65159083

x: -0.02663520927365458, y: -0.02241115784176269 z: 6.108281362555693
x: -0.02166564201134531, y: -0.021461074385831103 z: 5.934926291892719
x: -0.018459225950778216, y: -0.019057539834994475 z: 5.759127570948881
x: -0.0179352361062489, y: -0.016007115186013155 z: 5.580388578582415
x: -0.020298157821782202, y: -0.013414265400064915 z: 5.398237465361074
x: -0.02514623301848976, y: -0.012332040253454732 z: 5.212407529366349
x: -0.03171809238493183, y: -0.01357954571416473 z: 5.022858318695092
x: -0.03898319765896387, y: -0.017612977431863144 z: 4.829735571602378
x: -0.04579648313274155, y: -0.024443248250281678 z: 4.633293298880108
x: -0.051094963042919016, y: -0.03362014585165347 z: 4.433784574227558
x: -0.054057547786628454, y: -0.0442788589000808 z: 4.231355918975312
x: -0.05424155588126659, y: -0.05528935323769761 z: 4.0259622895738785
x: -0.05168433562102241, y: -0.06545570183163739 z: 3.817341661618065
x: -0.04690708469902248, y: -0.07378198025885191 z: 3.605075103244842
x: -0.0407

x: -0.0006239359890902056, y: -0.04381846913621567 z: 9.588803080024364
x: -0.0008061724806594173, y: -0.046489689569782465 z: 9.537287965779642
x: -0.00102271956331989, y: -0.04528455035519738 z: 9.481214329494293
x: -0.0012765312581471309, y: -0.04109492504806329 z: 9.4187565734608
x: -0.0015707498436070737, y: -0.0356058656445993 z: 9.348782014915264
x: -0.0019091862470853192, y: -0.03080328050687395 z: 9.271115986358257
x: -0.00229649779264248, y: -0.028515487795715708 z: 9.18654706400317
x: -0.002738559639171599, y: -0.03001180703469605 z: 9.096654919829886
x: -0.0032402294167581773, y: -0.035521182617347734 z: 9.003510614221769
x: -0.0038037082389078577, y: -0.044010835385484705 z: 8.908994610065239
x: -0.00443128740449736, y: -0.053635291866145525 z: 8.814186392291493
x: -0.005127344807623564, y: -0.062329107709550344 z: 8.7191653286221
x: -0.0058987460594353384, y: -0.06822698648542612 z: 8.623055305493324
x: -0.0067501568414650845, y: -0.07027608019593372 z: 8.52414604123871
x

x: 0.030556705536692347, y: -0.30788775200027985 z: 3.1162915158433884
x: 0.03332554867354007, y: -0.32300687727638067 z: 2.881221466301741
x: 0.03627736966446349, y: -0.3376624987362631 z: 2.644485358086871
x: 0.03950772997900573, y: -0.3502675976366537 z: 2.4063738284843854
x: 0.0431109518488205, y: -0.35932297179474143 z: 2.1662492875678545
x: 0.04706801256442171, y: -0.36509776082000245 z: 1.9220747299117529
x: 0.05125349834594247, y: -0.3694763423138628 z: 1.6727271469334883
x: 0.0556351586949216, y: -0.37396064368056736 z: 1.4180337822241924
x: 0.06040130267191196, y: -0.3796665663815049 z: 1.1572568310272335
x: 0.06582003503944069, y: -0.38836855368381673 z: 0.8902240471702665
x: 0.07204647273923956, y: -0.40126779993240763 z: 0.6184107195854321
x: 0.07892057198391876, y: -0.41737742637753417 z: 0.34364715193830364
x: 0.08610891438059838, y: -0.434614042793728 z: 0.0663685046644616
x: 0.09345183179874599, y: -0.45182246931590697 z: 0.0
x: 0.10111752951982059, y: -0.4676980659218

...

x: -0.476433168521484, y: 0.5016678488978085 z: 46.87241119396333
x: -0.4949158393078392, y: 0.5216133733297087 z: 47.42991743583682
x: -0.513841897970406, y: 0.5420352770218876 z: 47.98784259861704
x: -0.5332188435734887, y: 0.5629388808187998 z: 48.54616637940327
x: -0.5530535545887352, y: 0.5843285678880938 z: 49.104862125138936
x: -0.5733530615794977, y: 0.6062087612360657 z: 49.663904572360714
x: -0.5941252050516752, y: 0.6285848200307955 z: 50.223277111227524
x: -0.6153775347719771, y: 0.6514617252111408 z: 50.782961637378676
x: -0.6371175900757109, y: 0.6748444037271554 z: 51.34294087028731
x: -0.6593528937803804, y: 0.698737933968905 z: 51.90320039797429
x: -0.6820902023672529, y: 0.7231468571282763 z: 52.463724151190895
x: -0.705335743835741, y: 0.7480755336041405 z: 53.02449652014409
x: -0.7290954219282113, y: 0.7735282451197518 z: 53.58550416491881
x: -0.753374933410777, y: 0.799509134124857 z: 54.146736902556285
x: -0.7781793498490747, y: 0.8260217067940808 z: 54.7081842975

x: -9.532525507427827, y: 10.471540972472667 z: 114.91999227317129
x: -9.760593774705987, y: 10.661767757354825 z: 115.29092992389549
x: -9.996371776237313, y: 10.86026889112278 z: 115.6474114400092
x: -10.239964335243304, y: 11.05651155564163 z: 115.98849240774848
x: -10.491003812812771, y: 11.244905814712403 z: 116.31788805860944
x: -10.746613991337245, y: 11.429859117318124 z: 116.64260621376447
x: -11.00678420084184, y: 11.621438397665818 z: 116.9616795241133
x: -11.275096775224476, y: 11.814230844480909 z: 117.26741954886266
x: -11.551084403384799, y: 12.009266639520535 z: 117.5653025101269
x: -11.834988754830935, y: 12.20514004570088 z: 117.8562865957949
x: -12.126202274090279, y: 12.392645925502567 z: 118.14265617237866
x: -12.423787407030929, y: 12.581761894876546 z: 118.42446026886903
x: -12.72938197947726, y: 12.769011241978738 z: 118.6971438201298
x: -13.041734935104465, y: 12.950494305128826 z: 118.97076066458426
x: -13.362162908953989, y: 13.128674151098222 z: 119.23942794

Episode: 996  Reward: -60.070735675087505 highScore: 217.99116933142315
x: 0.0, y: 0.0 z: 10.0
x: 0.0, y: 0.0 z: 10.005341511190863
x: -2.0449390626187587e-08, y: 0.004010491736509935 z: 10.020163905153366
x: -4.4759507652187446e-07, y: 0.018218264075889532 z: 10.041031453598078
x: -2.355923329835579e-06, y: 0.04421195794774352 z: 10.066494455633688
x: -7.512668512938756e-06, y: 0.07481465882898618 z: 10.099905641668977
x: -1.8374566146086785e-05, y: 0.0983173124611909 z: 10.132708849437062
x: -3.8130493062130176e-05, y: 0.1224237256017638 z: 10.160508971598633
x: -7.068664761422366e-05, y: 0.1497048288048958 z: 10.180868821797459
x: -0.00012073356191040748, y: 0.16819538584853344 z: 10.196033151028484
x: -0.0001937547853146208, y: 0.18531822266432027 z: 10.218509636832632
x: -0.00029595822366592164, y: 0.21360954148308547 z: 10.242950381990708
x: -0.0004338881515381266, y: 0.25381090586113564 z: 10.257542758458834
x: -0.0006139381922980074, y: 0.2983515780137706 z: 10.255271231185677


x: 0.054661581394255046, y: 1.6024676724360818 z: 9.155961551042646
x: 0.06032075267669738, y: 1.6419927729330068 z: 8.993985956489542
x: 0.06637817042969396, y: 1.6670041787507035 z: 8.817338303218975
x: 0.07284098634291994, y: 1.6735484545219268 z: 8.63689278287981
x: 0.07965124097488459, y: 1.6663177268781313 z: 8.460529645553958
x: 0.0867575672842, y: 1.6482965302918091 z: 8.281779027784882
x: 0.09416789508564787, y: 1.6311606213523273 z: 8.093702935283936
x: 0.10193222593199865, y: 1.611422089063306 z: 7.901139590796465
x: 0.11007713658032013, y: 1.5870824406052135 z: 7.7133920156862645
x: 0.11858781872836907, y: 1.576372410899459 z: 7.5248200667418566
x: 0.12744699405191975, y: 1.5738282803227843 z: 7.319188818709957
x: 0.13662982415977581, y: 1.5635912965616554 z: 7.095011599696461
x: 0.1461295432797494, y: 1.5363231053424709 z: 6.861253750964914
x: 0.15592081916982906, y: 1.4917001599660211 z: 6.629282181064949
x: 0.16596126659984578, y: 1.4360791806980358 z: 6.407073999204819


x: 0.0, y: 0.0 z: 10.0
x: 0.0, y: 0.0 z: 10.005344611919334
x: -4.086530188773839e-08, y: 0.004075717106074526 z: 10.020133598479351
x: 2.840554533021695e-07, y: 0.018494417687730257 z: 10.040802646766851
x: 2.3551665834222115e-06, y: 0.04491528766322658 z: 10.065779510791486
x: 8.555047769732531e-06, y: 0.07642124902062856 z: 10.098583565662363
x: 2.2056900806130985e-05, y: 0.10093943789003085 z: 10.13119410415385
x: 4.66477709256722e-05, y: 0.12601825461869906 z: 10.15870354561387
x: 8.648481614406232e-05, y: 0.1539626953687201 z: 10.178600215227801
x: 0.00014700197449633403, y: 0.17307118291922072 z: 10.194033972441787
x: 0.00023596529287392892, y: 0.19179621567848165 z: 10.216846267567881
x: 0.0003635570838609315, y: 0.22217269815759075 z: 10.240572231660362
x: 0.0005420811903605497, y: 0.26384018097308287 z: 10.253340280381392
x: 0.0007853575444150601, y: 0.3085587472224262 z: 10.248879202179
x: 0.001108624054928477, y: 0.34706267289931336 z: 10.228154601063856
x: 0.00152866838483


## Plot the Rewards

Once you are satisfied with your performance, plot the episode rewards, either from a single run, or averaged over multiple runs. 

In [ ]:
## TODO: Plot the rewards.

## Reflections

**Question 1**: Describe the task that you specified in `task.py`.  How did you design the reward function?

**Answer**:

**Question 2**: Discuss your agent briefly, using the following questions as a guide:

- What learning algorithm(s) did you try? What worked best for you?
- What was your final choice of hyperparameters (such as $\alpha$, $\gamma$, $\epsilon$, etc.)?
- What neural network architecture did you use (if any)? Specify layers, sizes, activation functions, etc.

**Answer**:

**Question 3**: Using the episode rewards plot, discuss how the agent learned over time.

- Was it an easy task to learn or hard?
- Was there a gradual learning curve, or an aha moment?
- How good was the final performance of the agent? (e.g. mean rewards over the last 10 episodes)

**Answer**:

**Question 4**: Briefly summarize your experience working on this project. You can use the following prompts for ideas.

- What was the hardest part of the project? (e.g. getting started, plotting, specifying the task, etc.)
- Did you find anything interesting in how the quadcopter or your agent behaved?

**Answer**: